### Import dependencies 

In [1]:
import warnings
warnings.filterwarnings('ignore')

In [2]:
import numpy as np
import pandas as pd
import requests
from pathlib import Path
from collections import Counter
pd.set_option("display.max_rows", None, "display.max_columns", None)

### Read Crime Data from Datasources

In [3]:
gainesville_crime_data = "C:/Users/szieg/Repositories/FinalProject/Gainesville_Crime/Gainesville_Crime/Gainesville_Crime.csv"
classifications = "C:/Users/szieg/Repositories/FinalProject/Gainesville_Crime/Classifications.csv"


In [4]:
# Read Gainesville_Crime.csv
gainesville_df = pd.read_csv(gainesville_crime_data)
gainesville_df.head()

ID                Incident Type     Report Date    Offense Date  \
0  221009134          Assist Other Agency   7/2/2021 1:00   7/2/2021 1:00   
1  221009267  Domestic Aggravated Battery  7/4/2021 22:37  7/4/2021 21:24   
2  221009201          Assist Other Agency  7/3/2021 12:31  7/3/2021 12:25   
3  121009277               Assist Citizen   7/5/2021 3:27   7/5/2021 3:27   
4  221009177               Warrant Arrest  7/2/2021 18:51  7/2/2021 18:51   

   Report Hour of Day Report Day of Week  Offense Hour of Day  \
0                   1             Friday                    1   
1                  22             Sunday                   21   
2                  12           Saturday                   12   
3                   3             Monday                    3   
4                  18             Friday                   18   

  Offense Day of Week         City State                  Address   Latitude  \
0              Friday  GAINESVILLE    FL  300 BLK SW WILLISTON RD  29.620543   
1              Sunday  GAINESVILLE    FL      100 BLK NW 39TH AVE  29.688534   
2            Saturday  GAINESVILLE    FL      200 BLK SE 16TH AVE  29.634039   
3              Monday  GAINESVILLE    FL       500 BLK NW 8TH AVE  29.659423   
4              Friday  GAINESVILLE    FL       1500 BLK N MAIN ST  29.665770   

   Longitude                               Location  
0 -82.328759  POINT (-82.328759 29.620542999999998)  
1 -82.326069  POINT (-82.326069 29.688534000000004)  
2 -82.326408  POINT (-82.326408 29.634038999999998)  
3 -82.329994           POINT (-82.329994 29.659423)  
4 -82.324505            POINT (-82.324505 29.66577)

### Clean Gainesville Crime data

In [5]:
# Rename column headers for Gainesville crime

gainesville_df.rename(columns = {'Incident Type': 'CFS',
                                 'Report Date' : 'reportDate',
                                 'Offense Date' : 'offenseDate',
                                 'Report Hour of Day' : 'reportHour',
                                 'Report Day of Week' : 'reportDOW',
                                 'Offense Hour of Day' : 'offenseHour',
                                 'Offense Day of Week' : 'offenseDOW',
                                 'City' : 'city',
                                 'State' : 'state',
                                 'Address' : 'CFSaddress',
                                 'Latitude' : 'CFSlatitude',
                                 'Longitude' : 'CFSlongitude',
                                 'Location' : 'CFSlocation'
                                                            
                                }, inplace = True)


gainesville_df.head()

ID                          CFS      reportDate     offenseDate  \
0  221009134          Assist Other Agency   7/2/2021 1:00   7/2/2021 1:00   
1  221009267  Domestic Aggravated Battery  7/4/2021 22:37  7/4/2021 21:24   
2  221009201          Assist Other Agency  7/3/2021 12:31  7/3/2021 12:25   
3  121009277               Assist Citizen   7/5/2021 3:27   7/5/2021 3:27   
4  221009177               Warrant Arrest  7/2/2021 18:51  7/2/2021 18:51   

   reportHour reportDOW  offenseHour offenseDOW         city state  \
0           1    Friday            1     Friday  GAINESVILLE    FL   
1          22    Sunday           21     Sunday  GAINESVILLE    FL   
2          12  Saturday           12   Saturday  GAINESVILLE    FL   
3           3    Monday            3     Monday  GAINESVILLE    FL   
4          18    Friday           18     Friday  GAINESVILLE    FL   

                CFSaddress  CFSlatitude  CFSlongitude  \
0  300 BLK SW WILLISTON RD    29.620543    -82.328759   
1      100 BLK NW 39TH AVE    29.688534    -82.326069   
2      200 BLK SE 16TH AVE    29.634039    -82.326408   
3       500 BLK NW 8TH AVE    29.659423    -82.329994   
4       1500 BLK N MAIN ST    29.665770    -82.324505   

                             CFSlocation  
0  POINT (-82.328759 29.620542999999998)  
1  POINT (-82.326069 29.688534000000004)  
2  POINT (-82.326408 29.634038999999998)  
3           POINT (-82.329994 29.659423)  
4            POINT (-82.324505 29.66577)

In [6]:
#Drop unneeded columns
gainesville_df= gainesville_df.drop(['reportDate', 'reportHour', 'reportDOW','city','state','CFSlocation'],axis=1)
gainesville_df.head()

ID                          CFS     offenseDate  offenseHour  \
0  221009134          Assist Other Agency   7/2/2021 1:00            1   
1  221009267  Domestic Aggravated Battery  7/4/2021 21:24           21   
2  221009201          Assist Other Agency  7/3/2021 12:25           12   
3  121009277               Assist Citizen   7/5/2021 3:27            3   
4  221009177               Warrant Arrest  7/2/2021 18:51           18   

  offenseDOW               CFSaddress  CFSlatitude  CFSlongitude  
0     Friday  300 BLK SW WILLISTON RD    29.620543    -82.328759  
1     Sunday      100 BLK NW 39TH AVE    29.688534    -82.326069  
2   Saturday      200 BLK SE 16TH AVE    29.634039    -82.326408  
3     Monday       500 BLK NW 8TH AVE    29.659423    -82.329994  
4     Friday       1500 BLK N MAIN ST    29.665770    -82.324505

In [7]:
# Filter Gainesville_Crimes.csv for date range
start_date = '01-01-2018'
end_date = '12-31-2021'
gainesville_df['offenseDate'] = pd.to_datetime(gainesville_df['offenseDate'])
date_range = (gainesville_df['offenseDate'] > start_date) & (gainesville_df['offenseDate'] <= end_date)
gainesville_df = gainesville_df.loc[date_range]
gainesville_df['offenseDate'] = pd.to_datetime(gainesville_df['offenseDate']).dt.date
gainesville_df.head()


ID                          CFS offenseDate  offenseHour offenseDOW  \
0  221009134          Assist Other Agency  2021-07-02            1     Friday   
1  221009267  Domestic Aggravated Battery  2021-07-04           21     Sunday   
2  221009201          Assist Other Agency  2021-07-03           12   Saturday   
3  121009277               Assist Citizen  2021-07-05            3     Monday   
4  221009177               Warrant Arrest  2021-07-02           18     Friday   

                CFSaddress  CFSlatitude  CFSlongitude  
0  300 BLK SW WILLISTON RD    29.620543    -82.328759  
1      100 BLK NW 39TH AVE    29.688534    -82.326069  
2      200 BLK SE 16TH AVE    29.634039    -82.326408  
3       500 BLK NW 8TH AVE    29.659423    -82.329994  
4       1500 BLK N MAIN ST    29.665770    -82.324505

### Read Classification data from datasource

In [8]:
# Read Classifications.csv
classifications_df = pd.read_csv(classifications)
classifications_df.head()

CFS CFS_Type Classification
0                      Driving Under the Influence  Alcohol     Government
1                    Poss. of Alcohol Under 21 Yoa  Alcohol     Government
2                       All Other Liquor Law Viol.  Alcohol     Government
3  Alcohol Beverage-possess by Person Under 21 Yoa  Alcohol     Government
4              Assault (police Officer Aggravated)  Assault         Person

In [9]:
#Create CSV file for classifications_df data
#classifications_df.to_csv('Classification.csv',index=False)

### Access API for moonphase data

In [10]:
url = 'https://weather.visualcrossing.com/VisualCrossingWebServices/rest/services/timeline/Gainesville,FL/2018-01-01/2021-12-31?unitGroup=us&key=JVFDPCT4LWWPVKADN783XGRVA&include=days&elements=datetime,moonphase'
r = requests.get(url)
json = r.json()
json

{'queryCost': 1461,
 'latitude': 29.652,
 'longitude': -82.3228,
 'resolvedAddress': 'Gainesville, FL, United States',
 'address': 'Gainesville,FL',
 'timezone': 'America/New_York',
 'tzoffset': -5.0,
 'days': [{'datetime': '2018-01-01', 'moonphase': 0.5},
  {'datetime': '2018-01-02', 'moonphase': 0.5},
  {'datetime': '2018-01-03', 'moonphase': 0.52},
  {'datetime': '2018-01-04', 'moonphase': 0.54},
  {'datetime': '2018-01-05', 'moonphase': 0.58},
  {'datetime': '2018-01-06', 'moonphase': 0.63},
  {'datetime': '2018-01-07', 'moonphase': 0.68},
  {'datetime': '2018-01-08', 'moonphase': 0.73},
  {'datetime': '2018-01-09', 'moonphase': 0.78},
  {'datetime': '2018-01-10', 'moonphase': 0.83},
  {'datetime': '2018-01-11', 'moonphase': 0.88},
  {'datetime': '2018-01-12', 'moonphase': 0.92},
  {'datetime': '2018-01-13', 'moonphase': 0.95},
  {'datetime': '2018-01-14', 'moonphase': 0.98},
  {'datetime': '2018-01-15', 'moonphase': 0.99},
  {'datetime': '2018-01-16', 'moonphase': 1.0},
  {'dateti

In [11]:
json.keys()

dict_keys(['queryCost', 'latitude', 'longitude', 'resolvedAddress', 'address', 'timezone', 'tzoffset', 'days'])

In [12]:
moonphases_df = pd.DataFrame(json['days'])
moonphases_df.head()

datetime  moonphase
0  2018-01-01       0.50
1  2018-01-02       0.50
2  2018-01-03       0.52
3  2018-01-04       0.54
4  2018-01-05       0.58

In [13]:
json['days']

[{'datetime': '2018-01-01', 'moonphase': 0.5},
 {'datetime': '2018-01-02', 'moonphase': 0.5},
 {'datetime': '2018-01-03', 'moonphase': 0.52},
 {'datetime': '2018-01-04', 'moonphase': 0.54},
 {'datetime': '2018-01-05', 'moonphase': 0.58},
 {'datetime': '2018-01-06', 'moonphase': 0.63},
 {'datetime': '2018-01-07', 'moonphase': 0.68},
 {'datetime': '2018-01-08', 'moonphase': 0.73},
 {'datetime': '2018-01-09', 'moonphase': 0.78},
 {'datetime': '2018-01-10', 'moonphase': 0.83},
 {'datetime': '2018-01-11', 'moonphase': 0.88},
 {'datetime': '2018-01-12', 'moonphase': 0.92},
 {'datetime': '2018-01-13', 'moonphase': 0.95},
 {'datetime': '2018-01-14', 'moonphase': 0.98},
 {'datetime': '2018-01-15', 'moonphase': 0.99},
 {'datetime': '2018-01-16', 'moonphase': 1.0},
 {'datetime': '2018-01-17', 'moonphase': 0.0},
 {'datetime': '2018-01-18', 'moonphase': 0.01},
 {'datetime': '2018-01-19', 'moonphase': 0.03},
 {'datetime': '2018-01-20', 'moonphase': 0.05},
 {'datetime': '2018-01-21', 'moonphase': 0.0

### Transform moonphase data 

In [14]:
bins = [-np.inf , .25 , .50 , .75, 1 ]
moonphases_df['moonPhases_cat'] = pd.cut(moonphases_df['moonphase'], bins)
labels =['New Moon','First Quarter','Third Quarter','Full Moon']
moonphases_df['moonPhases'] = pd.cut(moonphases_df['moonphase'], bins,labels=labels)
moonphases_df.head(1000)
moonphases_df.dtypes

datetime            object
moonphase          float64
moonPhases_cat    category
moonPhases        category
dtype: object

In [15]:
#moonphases_df['datetime'] = pd.to_datetime(moonphases_df['datetime'])
#moonphases_df.dtypes

In [16]:
new_moonphasesdf = moonphases_df[['datetime','moonPhases']]
new_moonphasesdf.head(50)


datetime     moonPhases
0   2018-01-01  First Quarter
1   2018-01-02  First Quarter
2   2018-01-03  Third Quarter
3   2018-01-04  Third Quarter
4   2018-01-05  Third Quarter
5   2018-01-06  Third Quarter
6   2018-01-07  Third Quarter
7   2018-01-08  Third Quarter
8   2018-01-09      Full Moon
9   2018-01-10      Full Moon
10  2018-01-11      Full Moon
11  2018-01-12      Full Moon
12  2018-01-13      Full Moon
13  2018-01-14      Full Moon
14  2018-01-15      Full Moon
15  2018-01-16      Full Moon
16  2018-01-17       New Moon
17  2018-01-18       New Moon
18  2018-01-19       New Moon
19  2018-01-20       New Moon
20  2018-01-21       New Moon
21  2018-01-22       New Moon
22  2018-01-23       New Moon
23  2018-01-24       New Moon
24  2018-01-25  First Quarter
25  2018-01-26  First Quarter
26  2018-01-27  First Quarter
27  2018-01-28  First Quarter
28  2018-01-29  First Quarter
29  2018-01-30  First Quarter
30  2018-01-31  First Quarter
31  2018-02-01  Third Quarter
32  2018-02-02  Third Quarter
33  2018-02-03  Third Quarter
34  2018-02-04  Third Quarter
35  2018-02-05  Third Quarter
36  2018-02-06  Third Quarter
37  2018-02-07  Third Quarter
38  2018-02-08      Full Moon
39  2018-02-09      Full Moon
40  2018-02-10      Full Moon
41  2018-02-11      Full Moon
42  2018-02-12      Full Moon
43  2018-02-13      Full Moon
44  2018-02-14      Full Moon
45  2018-02-15      Full Moon
46  2018-02-16       New Moon
47  2018-02-17       New Moon
48  2018-02-18       New Moon
49  2018-02-19       New Moon

In [17]:
new_moonphasesdf.rename(columns={'datetime': 'Date'}, inplace=True)
new_moonphasesdf.head()

Date     moonPhases
0  2018-01-01  First Quarter
1  2018-01-02  First Quarter
2  2018-01-03  Third Quarter
3  2018-01-04  Third Quarter
4  2018-01-05  Third Quarter

In [18]:
new_moonphasesdf['Date'] = pd.to_datetime(new_moonphasesdf.Date, format='%Y-%m-%d')

In [19]:
new_moonphasesdf['Date'] = pd.to_datetime(new_moonphasesdf['Date']).dt.date
new_moonphasesdf.head()

Date     moonPhases
0  2018-01-01  First Quarter
1  2018-01-02  First Quarter
2  2018-01-03  Third Quarter
3  2018-01-04  Third Quarter
4  2018-01-05  Third Quarter

### Merge data

In [20]:
# Merge Gainesville Crime with Classification for CFS_Type and Classifications

gainesville_classified_df = pd.merge(gainesville_df, classifications_df, how= "inner", on=["CFS"])
gainesville_classified_df = gainesville_classified_df[['ID', 'CFS','CFS_Type', 'Classification', 'offenseDate',
                                                      'offenseHour','offenseDOW','CFSaddress','CFSlatitude','CFSlongitude']]
gainesville_classified_df.head()
gainesville_classified_df.dtypes



ID                  int64
CFS                object
CFS_Type           object
Classification     object
offenseDate        object
offenseHour         int64
offenseDOW         object
CFSaddress         object
CFSlatitude       float64
CFSlongitude      float64
dtype: object

In [21]:
# Merged the MoonPhases data with Gainesville Crime and Classifications

gainesville_classified_moon_df = pd.merge(gainesville_classified_df, new_moonphasesdf, how='left', left_on='offenseDate', right_on='Date')

gainesville_classified_moon_df.head(5000)

ID                             CFS         CFS_Type  \
0      221009267     Domestic Aggravated Battery          Battery   
1      221009608     Domestic Aggravated Battery          Battery   
2      221009391     Domestic Aggravated Battery          Battery   
3      221009308     Domestic Aggravated Battery          Battery   
4      221011388     Domestic Aggravated Battery          Battery   
5      221011524     Domestic Aggravated Battery          Battery   
6      221012057     Domestic Aggravated Battery          Battery   
7      221012231     Domestic Aggravated Battery          Battery   
8      221012341     Domestic Aggravated Battery          Battery   
9      221013249     Domestic Aggravated Battery          Battery   
10     221014033     Domestic Aggravated Battery          Battery   
11     221014308     Domestic Aggravated Battery          Battery   
12     221014905     Domestic Aggravated Battery          Battery   
13     221015541     Domestic Aggravated Battery          Battery   
14     221015627     Domestic Aggravated Battery          Battery   
15     221015394     Domestic Aggravated Battery          Battery   
16     221016364     Domestic Aggravated Battery          Battery   
17     221016505     Domestic Aggravated Battery          Battery   
18     221017434     Domestic Aggravated Battery          Battery   
19     221017379     Domestic Aggravated Battery          Battery   
20     221017317     Domestic Aggravated Battery          Battery   
21     221018378     Domestic Aggravated Battery          Battery   
22     219009416     Domestic Aggravated Battery          Battery   
23     220018564     Domestic Aggravated Battery          Battery   
24     219021546     Domestic Aggravated Battery          Battery   
25     220006659     Domestic Aggravated Battery          Battery   
26     220003226     Domestic Aggravated Battery          Battery   
27     221005161     Domestic Aggravated Battery          Battery   
28     221005746     Domestic Aggravated Battery          Battery   
29     220005261     Domestic Aggravated Battery          Battery   
30     221001962     Domestic Aggravated Battery          Battery   
31     220018102     Domestic Aggravated Battery          Battery   
32     220010783     Domestic Aggravated Battery          Battery   
33     220004295     Domestic Aggravated Battery          Battery   
34     220011788     Domestic Aggravated Battery          Battery   
35     220011288     Domestic Aggravated Battery          Battery   
36     221000718     Domestic Aggravated Battery          Battery   
37     220014433     Domestic Aggravated Battery          Battery   
38     219010229     Domestic Aggravated Battery          Battery   
39     220018304     Domestic Aggravated Battery          Battery   
40     220008878     Domestic Aggravated Battery          Battery   
41     221001778     Domestic Aggravated Battery          Battery   
42     220012564     Domestic Aggravated Battery          Battery   
43     220017231     Domestic Aggravated Battery          Battery   
44     220009837     Domestic Aggravated Battery          Battery   
45     220000879     Domestic Aggravated Battery          Battery   
46     220003604     Domestic Aggravated Battery          Battery   
47     220004536     Domestic Aggravated Battery          Battery   
48     220004373     Domestic Aggravated Battery          Battery   
49     221006878     Domestic Aggravated Battery          Battery   
50     220012272     Domestic Aggravated Battery          Battery   
51     221004522     Domestic Aggravated Battery          Battery   
52     220006616     Domestic Aggravated Battery          Battery   
53     220003887     Domestic Aggravated Battery          Battery   
54     221006554     Domestic Aggravated Battery          Battery   
55     221004453     Domestic Aggravated Battery          Battery   
56     220010948     Domestic Aggravated Battery          Battery   
57     22000

In [22]:
#InciType = gainesville_df.loc[:,['incidentType']]

#InciType.head()

In [23]:
#df = pd.DataFrame(gainesville_df.incidentType.unique(), columns=['UniqueIncType'])
#df.head(230)

### Create CSV file 

In [24]:
#gainesville_classified_moon_df.to_csv('TransformGainesville_Crimes_MoonPhasesEachDatePandas.csv')